In [8]:
from ipyleaflet import (
    Map,
    Marker,
    TileLayer, ImageOverlay,
    Polyline, Polygon, Rectangle, Circle, CircleMarker,
    GeoJSON,
    DrawControl
)

In [2]:
%matplotlib notebook

In [3]:
center = [34.6252978589571, -77.34580993652344]
zoom = 10

In [ ]:
m = Map(center=center, zoom=zoom)
m

In [1]:
import matplotlib as mpl
import matplotlib.cm
import matplotlib.colors
import numpy as np

def n_colors(n, colormap=mpl.cm.Blues):
    data = np.linspace(0.0,1.0,n)
    c = [mpl.colors.rgb2hex(d[0:3]) for d in colormap(data)]
    return c

def data_to_colors(data, colormap=mpl.cm.Blues):
    c = [mpl.colors.rgb2hex(d[0:3]) for d in colormap(mpl.colors.Normalize()(data))]
    return c

In [1]:
import json
with open('demo.json') as f:
    data = json.load(f)

In [3]:
data

{u'features': [{u'geometry': {u'coordinates': [[[[-77.39940577291571,
        34.5780540544853],
       [-77.39940610066606, 34.57805427015046],
       [-77.39940640189788, 34.57805446836596],
       [-77.39940680648922, 34.57805473459376],
       [-77.39940687019617, 34.57805477651398],
       [-77.39940689381065, 34.57805472199389],
       [-77.3994073308358, 34.57805432604519],
       [-77.39940731720131, 34.578054179242265],
       [-77.39940728534575, 34.578053836252096],
       [-77.39940728147378, 34.57805380828763],
       [-77.39940726378504, 34.57805363205166],
       [-77.39940725501071, 34.57805361742678],
       [-77.39940719593868, 34.57805349818902],
       [-77.39940711258689, 34.57805350039165],
       [-77.39940706262787, 34.57805349996589],
       [-77.3994070238417, 34.578053501157314],
       [-77.39940689549977, 34.57805350509971],
       [-77.3994068702403, 34.5780535173504],
       [-77.39940683257294, 34.57805352755014],
       [-77.39940665584797, 34.578053512

In [3]:
n_features = len(data['features'])
colors = n_colors(n_features)
print n_features

20


In [4]:
colors

[u'#f7fbff',
 u'#edf4fc',
 u'#e3eef8',
 u'#d8e7f5',
 u'#cee0f2',
 u'#c2d9ee',
 u'#b2d2e8',
 u'#a0cbe2',
 u'#8cc0dd',
 u'#75b4d8',
 u'#63a8d3',
 u'#519ccc',
 u'#4090c5',
 u'#3282be',
 u'#2474b7',
 u'#1966ad',
 u'#0e59a2',
 u'#084b93',
 u'#083d7f',
 u'#08306b']

In [5]:
for feature, color in zip(data['features'], colors):
    feature['properties']['style'] = {'color':color, 'weight': 1, 'fillColor':color, 'fillOpacity':0.5}

In [6]:
data['features'][0]

{u'geometry': {u'coordinates': [[[[-77.39940577291571, 34.5780540544853],
     [-77.39940610066606, 34.57805427015046],
     [-77.39940640189788, 34.57805446836596],
     [-77.39940680648922, 34.57805473459376],
     [-77.39940687019617, 34.57805477651398],
     [-77.39940689381065, 34.57805472199389],
     [-77.3994073308358, 34.57805432604519],
     [-77.39940731720131, 34.578054179242265],
     [-77.39940728534575, 34.578053836252096],
     [-77.39940728147378, 34.57805380828763],
     [-77.39940726378504, 34.57805363205166],
     [-77.39940725501071, 34.57805361742678],
     [-77.39940719593868, 34.57805349818902],
     [-77.39940711258689, 34.57805350039165],
     [-77.39940706262787, 34.57805349996589],
     [-77.3994070238417, 34.578053501157314],
     [-77.39940689549977, 34.57805350509971],
     [-77.3994068702403, 34.5780535173504],
     [-77.39940683257294, 34.57805352755014],
     [-77.39940665584797, 34.57805351246129],
     [-77.39940650171212, 34.578053517196004],
     [

In [9]:
g = GeoJSON(data=data)

In [ ]:
g

In [ ]:
m.add_layer(g)

In [ ]:
m.remove_layer(g)

In [ ]:
g.close()

In [2]:
def df_to_geojson(df, properties, lat='latitude', lon='longitude'):
    geojson = {'type':'FeatureCollection', 'features':[]}
    for _, row in df.iterrows():
        feature = {'type':'Feature',
                   'properties':{},
                   'geometry':{'type':'Point',
                               'coordinates':[]}}
        feature['geometry']['coordinates'] = [row[lon],row[lat]]
        for prop in properties:
            feature['properties'][prop] = row[prop]
        geojson['features'].append(feature)
    return geojson

In [ ]:
cols = ['street_address', 'issue_type', 'status']
geojson = df_to_geojson(df, cols)

In [ ]:
output_filename = 'dataset.js'
with open(output_filename, 'wb') as output_file:
    output_file.write('var dataset = ')
    json.dump(geojson, output_file, indent=2)

In [1]:
import base64
import json
import numpy as np

class NumpyEncoder(json.JSONEncoder):

    def default(self, obj):
        """If input object is an ndarray it will be converted into a dict
        holding dtype, shape and the data, base64 encoded.
        """
        if isinstance(obj, np.ndarray):
            if obj.flags['C_CONTIGUOUS']:
                obj_data = obj.data
            else:
                cont_obj = np.ascontiguousarray(obj)
                assert(cont_obj.flags['C_CONTIGUOUS'])
                obj_data = cont_obj.data
            data_b64 = base64.b64encode(obj_data)
            return dict(__ndarray__=data_b64,
                        dtype=str(obj.dtype),
                        shape=obj.shape)
        # Let the base class default method raise the TypeError
        return json.JSONEncoder(self, obj)


def json_numpy_obj_hook(dct):
    """Decodes a previously encoded numpy ndarray with proper shape and dtype.

    :param dct: (dict) json encoded ndarray
    :return: (ndarray) if input was an encoded ndarray
    """
    if isinstance(dct, dict) and '__ndarray__' in dct:
        data = base64.b64decode(dct['__ndarray__'])
        return np.frombuffer(data, dct['dtype']).reshape(dct['shape'])
    return dct

expected = np.arange(100, dtype=np.float)
dumped = json.dumps(expected, cls=NumpyEncoder)
result = json.loads(dumped, object_hook=json_numpy_obj_hook)


# None of the following assertions will be broken.
assert result.dtype == expected.dtype, "Wrong Type"
assert result.shape == expected.shape, "Wrong Shape"
assert np.allclose(expected, result), "Wrong Values"
                                                          

In [2]:
expected

array([  0.,   1.,   2.,   3.,   4.,   5.,   6.,   7.,   8.,   9.,  10.,
        11.,  12.,  13.,  14.,  15.,  16.,  17.,  18.,  19.,  20.,  21.,
        22.,  23.,  24.,  25.,  26.,  27.,  28.,  29.,  30.,  31.,  32.,
        33.,  34.,  35.,  36.,  37.,  38.,  39.,  40.,  41.,  42.,  43.,
        44.,  45.,  46.,  47.,  48.,  49.,  50.,  51.,  52.,  53.,  54.,
        55.,  56.,  57.,  58.,  59.,  60.,  61.,  62.,  63.,  64.,  65.,
        66.,  67.,  68.,  69.,  70.,  71.,  72.,  73.,  74.,  75.,  76.,
        77.,  78.,  79.,  80.,  81.,  82.,  83.,  84.,  85.,  86.,  87.,
        88.,  89.,  90.,  91.,  92.,  93.,  94.,  95.,  96.,  97.,  98.,
        99.])

In [3]:
dumped

'{"dtype": "float64", "shape": [100], "__ndarray__": "AAAAAAAAAAAAAAAAAADwPwAAAAAAAABAAAAAAAAACEAAAAAAAAAQQAAAAAAAABRAAAAAAAAAGEAAAAAAAAAcQAAAAAAAACBAAAAAAAAAIkAAAAAAAAAkQAAAAAAAACZAAAAAAAAAKEAAAAAAAAAqQAAAAAAAACxAAAAAAAAALkAAAAAAAAAwQAAAAAAAADFAAAAAAAAAMkAAAAAAAAAzQAAAAAAAADRAAAAAAAAANUAAAAAAAAA2QAAAAAAAADdAAAAAAAAAOEAAAAAAAAA5QAAAAAAAADpAAAAAAAAAO0AAAAAAAAA8QAAAAAAAAD1AAAAAAAAAPkAAAAAAAAA/QAAAAAAAAEBAAAAAAACAQEAAAAAAAABBQAAAAAAAgEFAAAAAAAAAQkAAAAAAAIBCQAAAAAAAAENAAAAAAACAQ0AAAAAAAABEQAAAAAAAgERAAAAAAAAARUAAAAAAAIBFQAAAAAAAAEZAAAAAAACARkAAAAAAAABHQAAAAAAAgEdAAAAAAAAASEAAAAAAAIBIQAAAAAAAAElAAAAAAACASUAAAAAAAABKQAAAAAAAgEpAAAAAAAAAS0AAAAAAAIBLQAAAAAAAAExAAAAAAACATEAAAAAAAABNQAAAAAAAgE1AAAAAAAAATkAAAAAAAIBOQAAAAAAAAE9AAAAAAACAT0AAAAAAAABQQAAAAAAAQFBAAAAAAACAUEAAAAAAAMBQQAAAAAAAAFFAAAAAAABAUUAAAAAAAIBRQAAAAAAAwFFAAAAAAAAAUkAAAAAAAEBSQAAAAAAAgFJAAAAAAADAUkAAAAAAAABTQAAAAAAAQFNAAAAAAACAU0AAAAAAAMBTQAAAAAAAAFRAAAAAAABAVEAAAAAAAIBUQAAAAAAAwFRAAAAAAAAAVUAAAAAAAEBVQAAAAAAAgFVAAAAAAADAVUAAAAAAAA

In [4]:
result

array([  0.,   1.,   2.,   3.,   4.,   5.,   6.,   7.,   8.,   9.,  10.,
        11.,  12.,  13.,  14.,  15.,  16.,  17.,  18.,  19.,  20.,  21.,
        22.,  23.,  24.,  25.,  26.,  27.,  28.,  29.,  30.,  31.,  32.,
        33.,  34.,  35.,  36.,  37.,  38.,  39.,  40.,  41.,  42.,  43.,
        44.,  45.,  46.,  47.,  48.,  49.,  50.,  51.,  52.,  53.,  54.,
        55.,  56.,  57.,  58.,  59.,  60.,  61.,  62.,  63.,  64.,  65.,
        66.,  67.,  68.,  69.,  70.,  71.,  72.,  73.,  74.,  75.,  76.,
        77.,  78.,  79.,  80.,  81.,  82.,  83.,  84.,  85.,  86.,  87.,
        88.,  89.,  90.,  91.,  92.,  93.,  94.,  95.,  96.,  97.,  98.,
        99.])

In [4]:
import folium

In [1]:
import geopandas

In [7]:
b=geopandas.GeoDataFrame.from_file('../tmp/test.shp')

In [2]:
b=geopandas.GeoDataFrame.from_file('../../POPEXPO/geojson_1000316_9.geojson')

In [3]:
b

Class alertlevel                  description   eventname  \
0              Poly_Green        Red  Tropical Cyclone MATTHEW-16  MATTHEW-16   
1             Poly_Orange        Red  Tropical Cyclone MATTHEW-16  MATTHEW-16   
2                Poly_Red        Red  Tropical Cyclone MATTHEW-16  MATTHEW-16   
3   Poly_Polygon_Point_10        Red  Tropical Cyclone MATTHEW-16  MATTHEW-16   
4                Point_10       None                         None        None   
5   Poly_Polygon_Point_11        Red  Tropical Cyclone MATTHEW-16  MATTHEW-16   
6                Point_11       None                         None        None   
7   Poly_Polygon_Point_12        Red  Tropical Cyclone MATTHEW-16  MATTHEW-16   
8                Point_12       None                         None        None   
9   Poly_Polygon_Point_13        Red  Tropical Cyclone MATTHEW-16  MATTHEW-16   
10               Point_13       None                         None        None   
11  Poly_Polygon_Point_14        Red  Tropical Cyclone MATTHEW-16  MATTHEW-16   
12               Point_14       None                         None        None   
13  Poly_Polygon_Point_15        Red  Tropical Cyclone MATTHEW-16  MATTHEW-16   
14               Point_15       None                         None        None   
15   Poly_Polygon_Point_8        Red  Tropical Cyclone MATTHEW-16  MATTHEW-16   
16                Point_8       None                         None        None   
17   Poly_Polygon_Point_9        Red  Tropical Cyclone MATTHEW-16  MATTHEW-16   
18                Point_9       None                         None        None   
19            Line_Line_0        Red  Tropical Cyclone MATTHEW-16  MATTHEW-16   
20            Line_Line_1        Red  Tropical Cyclone MATTHEW-16  MATTHEW-16   
21            Line_Line_2        Red  Tropical Cyclone MATTHEW-16  MATTHEW-16   
22            Line_Line_3        Red  Tropical Cyclone MATTHEW-16  MATTHEW-16   
23            Line_Line_4        Red  Tropical Cyclone MATTHEW-16  MATTHEW-16   
24            Line_Line_5        Red  Tropical Cyclone MATTHEW-16  MATTHEW-16   
25            Line_Line_6        Red  Tropical Cyclone MATTHEW-16  MATTHEW-16   
26            Line_Line_7        Red  Tropical Cyclone MATTHEW-16  MATTHEW-16   
27            Line_Line_8        Red  Tropical Cyclone MATTHEW-16  MATTHEW-16   
28            Line_Line_9        Red  Tropical Cyclone MATTHEW-16  MATTHEW-16   
29           Line_Line_10        Red  Tropical Cyclone MATTHEW-16  MATTHEW-16   
30   Poly_Polygon_Point_0        Red  Tropical Cyclone MATTHEW-16  MATTHEW-16   
31                Point_0       None                         None        None   
32   Poly_Polygon_Point_1        Red  Tropical Cyclone MATTHEW-16  MATTHEW-16   
33                Point_1       None                         None        None   
34   Poly_Polygon_Point_2        Red  Tropical Cyclone MATTHEW-16  MATTHEW-16   
35                Point_2       None                         None        None   
36   Poly_Polygon_Point_3        Red  Tropical Cyclone MATTHEW-16  MATTHEW-16   
37                Point_3       None                         None        None   
38   Poly_Polygon_Point_4        Red  Tropical Cyclone MATTHEW-16  MATTHEW-16   
39                Point_4       None                         None        None   
40   Poly_Polygon_Point_5        Red  Tropical Cyclone MATTHEW-16  MATTHEW-16   
41                Point_5       None                         None        None   
42   Poly_Polygon_Point_6        Red  Tropical Cyclone MATTHEW-16  MATTHEW-16   
43                Point_6       None                         None        None   
44   Poly_Polygon_Point_7        Red  Tropical Cyclone MATTHEW-16  MATTHEW-16   
45                Point_7       None                         None        None   
46           Line_Line_11        Red  Tropical Cyclone MATTHEW-16  MATTHEW-16   
47           Line_Line_12        Red  Tropical Cyclone MATTHEW-16  MATTHEW-16   
48           Line_Line_13        Red  Tropical Cycl

In [8]:
m=folium.Map([20.,-75.],zoom_start=4)

In [9]:
folium.GeoJson(b).add_to(m)

In [10]:
m